In [1]:
import numpy as np
from scipy.spatial.distance import pdist, squareform
from matplotlib import pyplot as plt
from scipy.cluster.hierarchy import dendrogram, linkage

import plotly.offline as py
import plotly.graph_objs as go
from plotly.graph_objs import *
import plotly.figure_factory as FF

py.init_notebook_mode()

# Train Model

In [2]:
from gensim.models.ldamodel import LdaModel
from gensim.corpora import Dictionary, MmCorpus
import pandas as pd
import re
from gensim.parsing.preprocessing import remove_stopwords, strip_punctuation

Using TensorFlow backend.


In [3]:
df_fake = pd.read_csv('fake.csv')
df_fake[['title', 'text', 'language']].head()
df_fake = df_fake.loc[(pd.notnull(df_fake.text)) & (df_fake.language == 'english')]

# remove stopwords and punctuations
def preprocess(row):
    return strip_punctuation(remove_stopwords(row.lower()))
    
df_fake['text'] = df_fake['text'].apply(preprocess)

# Convert data to required input format by LDA
texts = []
for line in df_fake.text:
    lowered = line.lower()
    words = re.findall(r'\w+', lowered, flags = re.UNICODE | re.LOCALE)
    texts.append(words)
# Create a dictionary representation of the documents.
dictionary = Dictionary(texts)

# Filter out words that occur less than 2 documents, or more than 30% of the documents.
dictionary.filter_extremes(no_below=2, no_above=0.4)
# Bag-of-words representation of the documents.
corpus_fake = [dictionary.doc2bow(text) for text in texts]

In [19]:
lda_fake = LdaModel(corpus=corpus_fake, id2word=dictionary, num_topics=35, chunksize=1500, iterations=200, alpha='auto')
lda_fake.save('lda_35')

In [3]:
lda_fake = LdaModel.load('lda_35')

## Basic Dendrogram

In [4]:
from gensim.matutils import jenson_shannon

topic_dist = lda_fake.state.get_lambda()

def js_dist(X):
    return pdist(X, lambda u, v: jenson_shannon(u, v))

dendro = FF.create_dendrogram(topic_dist, distfun=js_dist, labels=range(1, 36))
dendro['layout'].update({'width':800, 'height':500})
py.iplot(dendro)

## Dendrogram with a Heatmap

In [5]:
# Initialize figure by creating upper dendrogram
figure = FF.create_dendrogram(topic_dist, orientation='bottom', distfun=js_dist, labels = range(1, 36))
for i in range(len(figure['data'])):
    figure['data'][i]['yaxis'] = 'y2'

In [6]:
mdiff, annotation = lda_fake.diff(lda_fake, distance="jenson_shannon", normed=False)

# get reordered topic list
dendro_leaves = figure['layout']['xaxis']['ticktext']
dendro_leaves = list(map(int, dendro_leaves-1))

# reorder distance matrix
heat_data = mdiff[dendro_leaves,:]
heat_data = heat_data[:,dendro_leaves]

In [8]:
annotation_html = [["+++ {}<br>--- {}".format(", ".join(int_tokens), 
                                          ", ".join(diff_tokens)) 
                        for (int_tokens, diff_tokens) in row] 
                       for row in annotation]

heatmap = go.Data([
    go.Heatmap(
        z = heat_data,
        colorscale = 'YIGnBu',
        text = annotation_html
    )
])

heatmap[0]['x'] = figure['layout']['xaxis']['tickvals']
heatmap[0]['y'] = figure['layout']['xaxis']['tickvals']

# Add Heatmap Data to Figure
figure['data'].extend(heatmap)

dendro_leaves = [x+1 for x in dendro_leaves]

# Edit Layout
figure['layout'].update({'width':800, 'height':800,
                         'showlegend':False, 'hovermode': 'closest',
                         })

# Edit xaxis
figure['layout']['xaxis'].update({'domain': [.25, 1],
                                  'mirror': False,
                                  'showgrid': False,
                                  'showline': False,
                                  "showticklabels": True, 
                                  "tickmode": "array",
                                  "ticktext" : dendro_leaves,
                                  "tickvals" : figure['layout']['xaxis']['tickvals'],
                                  'zeroline': False,
                                  'ticks':""})
# Edit xaxis2
figure['layout'].update({'xaxis2': {'domain': [0, .15],
                                   'mirror': False,
                                   'showgrid': False,
                                   'showline': False,
                                   'zeroline': False,
                                   'showticklabels': False,
                                   'ticks':""}})

# Edit yaxis
figure['layout']['yaxis'].update({'domain': [0, 0.75],
                                  'mirror': False,
                                  'showgrid': False,
                                  'showline': False,
                                  "showticklabels": True, 
                                  "tickmode": "array",
                                  "ticktext" : dendro_leaves,
                                  "tickvals" : figure['layout']['xaxis']['tickvals'],
                                  'zeroline': False,
                                  'ticks': ""})
# Edit yaxis2
figure['layout'].update({'yaxis2':{'domain':[0.75, 1],
                                   'mirror': False,
                                   'showgrid': False,
                                   'showline': False,
                                   'zeroline': False,
                                   'showticklabels': False,
                                   'ticks':""}})

py.iplot(figure)

In [10]:
import pyLDAvis as ldavis
import pyLDAvis.gensim
ldavis.enable_notebook()

viz = ldavis.gensim.prepare(lda_fake, corpus_fake, dictionary, sort_topics=False)
viz

/Users/parul/.virtualenvs/gensim3/lib/python3.4/site-packages/pyLDAvis/_prepare.py:387: DeprecationWarning:


.ix is deprecated. Please use
.loc for label based indexing or
.iloc for positional indexing

See the documentation here:
http://pandas.pydata.org/pandas-docs/stable/indexing.html#deprecate_ix



PreparedData(topic_coordinates=           Freq  cluster  topics         x         y
topic                                               
0      5.378490        1       1  0.081757 -0.087862
1      2.694626        1       2 -0.119995  0.113033
2      1.862549        1       3 -0.075064  0.112604
3      1.634658        1       4 -0.020012 -0.108075
4      3.700748        1       5 -0.091706  0.060846
5      2.557562        1       6  0.020360 -0.056178
6      2.143035        1       7 -0.103551  0.189966
7      4.614561        1       8 -0.012162  0.038499
8      4.764014        1       9 -0.058316 -0.062379
9      2.595867        1      10 -0.080691 -0.093027
10     2.856715        1      11  0.075622  0.010412
11     2.260897        1      12 -0.015045  0.005520
12     2.194664        1      13 -0.020592  0.029134
13     3.910268        1      14  0.237102 -0.045861
14     2.871468        1      15 -0.079086  0.062621
15     2.592763        1      16 -0.021237 -0.136292
16     1.961201        1      17 -0.091307 -0.159086
17     3.847650        1      18  0.024322 -0.129454
18     3.507668        1      19  0.137300 -0.034811
19     1.711436        1      20  0.061804  0.023412
20     3.927512        1      21  0.157666  0.039416
21     3.089577        1      22  0.078660  0.021673
22     2.193935        1      23  0.001203  0.084984
23     1.478392        1      24 -0.042901  0.134619
24     3.833267        1      25 -0.037547  0.054079
25     2.785812        1      26  0.004891 -0.041195
26     3.563507        1      27 -0.087578 -0.057885
27     1.581778        1      28 -0.149148 -0.189346
28     2.147545        1      29 -0.029912  0.040717
29     2.685023        1      30 -0.048719  0.045045
30     2.394444        1      31  0.057669  0.097867
31     2.179527        1      32  0.048077  0.005290
32     2.211573        1      33 -0.052363 -0.020788
33     2.979830        1      34  0.229617  0.045721
34     3.287435        1      35  0.020882  0.006782, topic_info=      Category          Freq            Term         Total  loglift  logprob
term                                                                        
29492  Default  13809.000000           taxed  13809.000000  30.0000  30.0000
23747  Default   9001.000000            damp   9001.000000  29.0000  29.0000
8522   Default  12135.000000     privatizers  12135.000000  28.0000  28.0000
1172   Default   5205.000000       timeframe   5205.000000  27.0000  27.0000
33220  Default   8929.000000            rene   8929.000000  26.0000  26.0000
19816  Default   3074.000000      concoction   3074.000000  25.0000  25.0000
24475  Default   2979.000000       reminders   2979.000000  24.0000  24.0000
5573   Default   3215.000000     accomplices   3215.000000  23.0000  23.0000
10930  Default   5757.000000          infirm   5757.000000  22.0000  22.0000
12910  Default   6722.000000      deplorable   6722.000000  21.0000  21.0000
45372  Default   5152.000000     revisionism   5152.000000  20.0000  20.0000
45343  Default   4095.000000    overcharging   4095.000000  19.0000  19.0000
50095  Default   3134.000000          geared   3134.000000  18.0000  18.0000
52458  Default   3587.000000           tower   3587.000000  17.0000  17.0000
49978  Default   2729.000000         memoirs   2729.000000  16.0000  16.0000
25136  Default   2902.000000    elaborations   2902.000000  15.0000  15.0000
20006  Default   3537.000000       certainty   3537.000000  14.0000  14.0000
7945   Default   2654.000000          vipers   2654.000000  13.0000  13.0000
43404  Default   3964.000000       defection   3964.000000  12.0000  12.0000
10671  Default   2726.000000        reminded   2726.000000  11.0000  11.0000
9415   Default   2044.000000       untrained   2044.000000  10.0000  10.0000
48555  Default   2611.000000      pestilence   2611.000000   9.0000   9.0000
43886  Default   3299.000000   discrepancies   3299.000000   8.0000   8.0000
38138  Default   2240.000000       remodeled   2240.000000   7.0000   7

In [9]:
def plot_difference(mdiff, title="", annotation=None):
    """
    Helper function for plot difference between models
    """
    annotation_html = None
    if annotation is not None:
        annotation_html = [["+++ {}<br>--- {}".format(", ".join(int_tokens), 
                                              ", ".join(diff_tokens)) 
                            for (int_tokens, diff_tokens) in row] 
                           for row in annotation]
        
    data = go.Heatmap(z=mdiff, colorscale='YIGnBu', text=annotation_html)
    layout = go.Layout(width=950, height=950, title=title,
                       xaxis=dict(title="topic"), yaxis=dict(title="topic"))
    py.iplot(dict(data=[data], layout=layout))

In [10]:
mdiff, annotation = lda_fake.diff(lda_fake, distance='jenson_shannon', num_words=50)
plot_difference(mdiff, title="Topic difference (one model) [jenson_shannon distance]", annotation=annotation)